In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

In [2]:
tf.logging.set_verbosity(tf.logging.INFO)

In [3]:
# model modes TRAIN, EVAL, PREDICT
def cnn_model_fn(features, labels, mode):
    '''Model fuction for CNN'''
    # Input Layer
    batch_size = -1
    image_width = 28
    image_height = 28
    # channel 1 for greyscale, 3 for rgb
    channels = 1
    input_layer = tf.reshape(
        features['x'],
        [batch_size, image_width,image_height, channels])

    # Convolutional Layer #1
    '''
    Applies 32 5x5 filters(extracting 5x5-pixel subregions),
    with ReLU activation function
    '''
    conv1 = tf.layers.conv2d(
        inputs=input_layer,
        filters=32,
        kernel_size=[5, 5],
        padding='same',
        activation=tf.nn.relu)

    # Pooling Layer #1
    '''
    Performs max pooling with a 2x2 filter and stride of 2
    (which specifies that pooled regions do not overlap)
    '''
    pool1 = tf.layers.max_pooling2d(
        inputs=conv1,
        pool_size=[2, 2],
        strides=2)

    # Convolutional Layer #2
    '''
    Applies 64 5x5 filters, with ReLU activation function
    '''
    conv2 = tf.layers.conv2d(
        inputs=pool1,
        filters=64,
        kernel_size=[5, 5],
        padding='same',
        activation=tf.nn.relu)

    # Pooling Layer #2
    '''
    Performs max pooling with a 2x2 filter and stride of 2
    '''
    pool2 = tf.layers.max_pooling2d(
        inputs=conv2,
        pool_size=[2, 2],
        strides=2)
    # Dense Layer
    '''
    1,024 neurons
    dropout regularization rate of 0.4
    (probability of 0.4 that any given element will be dropped in training)
    '''
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(
        inputs=pool2_flat,
        units=1024,
        activation=tf.nn.relu)
    dropout = tf.layers.dropout(
        inputs=dense,
        rate=0.4,
        training=mode == tf.estimator.ModeKeys.TRAIN)
    # Dense Layer #2 (Logits Layer)
    '''
    10 neurons, one for each digit target class (0–9)
    '''
    logits = tf.layers.dense(inputs=dropout, units=10)



    predictions = {
    # Generate predictions (for PREDICT & EVAL mode)
    'classes': tf.argmax(input=logits, axis=1),
    # Add softmax_tensor to the graph, used for PREDICT
    'probabilities': tf.nn.softmax(logits, name='softmax_tensor')
    }

    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for TRAIN & EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

    # Configure the Training Op (for Train mode)
    if(mode == tf.estimator.ModeKeys.TRAIN):
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
    'accuracy': tf.metrics.accuracy(
        labels=labels,
        predictions=predictions['classes'])
    }
    return tf.estimator.EstimatorSpec(
        mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


In [ ]:
def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset('mnist')
    train_data = mnist.train.images # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
        model_fn=cnn_model_fn, model_dir='/tmp/mnist_convnet_model')

    # Set up logging for predictions
    tensors_to_log = {'probabilities': 'softmax_tensor'}
    logging_hook = tf.train.LoggingTensorHook(
        tensors=tensors_to_log, every_n_iter=50)

    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={'x': train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])

    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={'x': eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)


In [7]:
if __name__ == '__main__':
  tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f034c46ff28>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_rep

INFO:tensorflow:loss = 0.058698375, step = 20002
INFO:tensorflow:probabilities = [[0.00002027 0.9974612  0.00079074 0.00008754 0.00007735 0.00001173
  0.00012487 0.00027208 0.00110675 0.00004747]
 [0.00001297 0.00146502 0.00739567 0.00150245 0.00000816 0.00007402
  0.00000017 0.98383117 0.00130361 0.00440664]
 [0.9963237  0.00002156 0.0003641  0.00006023 0.00000023 0.00191257
  0.00019963 0.00050541 0.00001917 0.00059342]
 [0.00006724 0.0000355  0.00001156 0.00000121 0.0002038  0.04810495
  0.9484373  0.0000001  0.00313295 0.00000542]
 [0.00583667 0.00044065 0.00784033 0.010858   0.00002201 0.94930077
  0.01559758 0.00004501 0.00707844 0.00298047]
 [0.00000226 0.00032483 0.00276862 0.00016736 0.00000027 0.00000175
  0.00000001 0.99346316 0.00237888 0.00089282]
 [0.00001137 0.0000013  0.00001347 0.00001556 0.00002502 0.00087496
  0.00000002 0.99723095 0.00001824 0.001809  ]
 [0.00000267 0.9835271  0.00036585 0.0014137  0.00156176 0.00022581
  0.00069194 0.00008046 0.01059918 0.00153151]

INFO:tensorflow:global_step/sec: 1.341
INFO:tensorflow:probabilities = [[0.00000003 0.00000048 0.00010587 0.00478856 0.98215574 0.00001865
  0.00002218 0.00000086 0.00047876 0.01242886]
 [0.00005182 0.00000682 0.12861414 0.00100998 0.00001547 0.00002791
  0.00008916 0.20909023 0.65675116 0.00434333]
 [0.999582   0.         0.00040712 0.00000059 0.00000001 0.00000208
  0.0000001  0.00000414 0.00000282 0.00000126]
 [0.000002   0.00000826 0.0000375  0.00000048 0.00009645 0.00008789
  0.9997253  0.00000001 0.00004165 0.00000047]
 [0.00003921 0.00000238 0.00001554 0.00005095 0.03998545 0.00057257
  0.00000291 0.0296174  0.00030322 0.9294104 ]
 [0.00000005 0.         0.00000108 0.00000001 0.99997115 0.00000052
  0.00002535 0.00000008 0.00000122 0.00000053]
 [0.00377323 0.08375082 0.01941416 0.71056545 0.00038891 0.00277555
  0.00045476 0.01007177 0.1626499  0.00615543]
 [0.00038423 0.00054289 0.01958723 0.02159749 0.00138854 0.00500958
  0.00014057 0.00195249 0.9482412  0.00115586]
 [0.00000

INFO:tensorflow:loss = 0.12955, step = 20102 (74.574 sec)
INFO:tensorflow:probabilities = [[0.0000168  0.9971847  0.00021321 0.00040487 0.00002973 0.00000986
  0.00002862 0.00161644 0.00044052 0.00005515]
 [0.00027622 0.99418265 0.00049263 0.00031665 0.00043192 0.00006064
  0.00046647 0.00056537 0.00296366 0.00024373]
 [0.0000003  0.00010181 0.99406886 0.00570956 0.00000027 0.00000143
  0.00000008 0.0000009  0.00011619 0.00000057]
 [0.00000617 0.00002883 0.99098724 0.00802064 0.00008194 0.00007816
  0.00000806 0.00000316 0.0007791  0.00000669]
 [0.00001025 0.0014858  0.00082031 0.88903254 0.0003032  0.0075854
  0.00003771 0.00004736 0.07772289 0.02295442]
 [0.99661714 0.00000009 0.00036433 0.00002699 0.00028396 0.00001102
  0.00043108 0.0000125  0.00177531 0.00047763]
 [0.00094041 0.41744474 0.05695854 0.01054144 0.18419193 0.00003301
  0.00210441 0.03873173 0.07794384 0.21110998]
 [0.00047241 0.9967044  0.00017425 0.00003548 0.00005393 0.00017948
  0.00032854 0.00039036 0.00163085 0.0

INFO:tensorflow:global_step/sec: 1.4231
INFO:tensorflow:probabilities = [[0.00002181 0.00957858 0.00194735 0.0097111  0.3079094  0.01049395
  0.00002974 0.40144902 0.01664757 0.24221145]
 [0.00130962 0.00000036 0.0000557  0.00007886 0.0000013  0.9948954
  0.00002743 0.00094293 0.00234132 0.00034713]
 [0.0025557  0.0003289  0.10441556 0.17273043 0.00020087 0.0434683
  0.01375048 0.00032926 0.6561515  0.00606898]
 [0.00062122 0.00000287 0.0014249  0.00004592 0.02289727 0.00023967
  0.00024494 0.00495648 0.0004222  0.9691445 ]
 [0.999368   0.00000015 0.00014901 0.00000096 0.00000032 0.00001952
  0.00008243 0.00000015 0.00000355 0.0003759 ]
 [0.00004287 0.00000053 0.9976236  0.00228031 0.00000003 0.00000028
  0.00000016 0.00005118 0.00000016 0.00000092]
 [0.9996942  0.00000011 0.00015281 0.00006326 0.00000214 0.00000317
  0.00006436 0.00000038 0.00001066 0.00000883]
 [0.00013776 0.00000175 0.00003427 0.00000034 0.00005494 0.00199346
  0.99762964 0.         0.00014747 0.0000004 ]
 [0.000000

...

INFO:tensorflow:global_step/sec: 1.40479
INFO:tensorflow:probabilities = [[0.00000028 0.00000038 0.00000134 0.00000017 0.9996984  0.00000172
  0.00000488 0.00000291 0.0000003  0.00028966]
 [0.00061359 0.00003342 0.00007143 0.00017367 0.00029738 0.00874667
  0.00001281 0.9534921  0.00025072 0.03630816]
 [0.00000011 0.00000003 0.00000072 0.00000473 0.         0.9998869
  0.00000088 0.00000001 0.00010101 0.00000566]
 [0.         0.00000099 0.00012673 0.9998325  0.         0.00000725
  0.         0.00000342 0.00002893 0.00000013]
 [0.00000186 0.00000007 0.00000792 0.00001507 0.00882141 0.000091
  0.00000004 0.00469436 0.0001842  0.98618406]
 [0.00000337 0.00011822 0.00071445 0.00004096 0.0000044  0.00418044
  0.00590514 0.00000022 0.98902285 0.00000992]
 [0.00000354 0.00002509 0.00010309 0.99644583 0.00000157 0.00307531
  0.00000765 0.00000222 0.00032622 0.00000952]
 [0.00000007 0.00000312 0.00000613 0.9997193  0.         0.00005244
  0.         0.         0.00021339 0.00000548]
 [0.989590

INFO:tensorflow:loss = 0.026289796, step = 39902 (71.178 sec)
INFO:tensorflow:probabilities = [[0.00000288 0.00000069 0.00000233 0.00000052 0.99996257 0.00001332
  0.00000168 0.000009   0.0000015  0.00000556]
 [0.00012134 0.0011831  0.10162821 0.770169   0.00001062 0.00017633
  0.00000231 0.07600502 0.04220721 0.00849673]
 [0.00011857 0.74921674 0.2276777  0.02129934 0.00000101 0.00009615
  0.00000217 0.00152568 0.00005561 0.00000706]
 [0.00000764 0.00000322 0.0000074  0.00000046 0.00008758 0.00047228
  0.9993981  0.00000002 0.00002332 0.00000003]
 [0.0000001  0.0000005  0.00004979 0.00132796 0.0000002  0.00000123
  0.00000001 0.00000018 0.9986119  0.00000806]
 [0.00047521 0.00026348 0.00210558 0.00048652 0.0780528  0.88616323
  0.00537948 0.02034693 0.00400869 0.00271809]
 [0.00037181 0.00091458 0.9762607  0.01299658 0.00000093 0.00001108
  0.00000628 0.0004566  0.00896858 0.00001287]
 [0.0324201  0.00005803 0.03100197 0.26905203 0.00058373 0.06578754
  0.00001698 0.0469634  0.5288278

INFO:tensorflow:Saving checkpoints for 40001 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.07586649.
INFO:tensorflow:Starting evaluation at 2018-03-18-02:43:17
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-40001
INFO:tensorflow:Finished evaluation at 2018-03-18-02:43:41
INFO:tensorflow:Saving dict for global step 40001: accuracy = 0.98, global_step = 40001, loss = 0.06312445
{'accuracy': 0.98, 'loss': 0.06312445, 'global_step': 40001}


SystemExit: 

/usr/local/lib/python3.6/dist-packages/IPython/core/interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
